# TP Reco n°2 : factorisation de matrices (ALS, SGD)

Le filtrage collaboratif, historiquement parmi les premiers algorithmes de recommandation, ne ressemble pas tout à fait à du _machine learning_, dans la mesure où l'on ne spécifie pas explicitement une fonction que l'on cherche à maximiser ou minimiser. Dans cette séance, nous allons aborder la factorisation de matrices, avec laquelle on apprend effectivement les paramètres d'un modèle en vue de minimiser _directement_ une fonction. 

## Préliminaires

On réutilisera les données de la séance précédente (Movielens), on disposera donc d'une matrice utilisateurs-films, avec des notes d'utilisateurs sur les films.

La factorisation de matrice suppose que :
- chaque utilisateur peut être décrit par $k$ attributs (par exemple : à quel point il/elle apprécie les films historiques
- chaque film peut être décrit par un ensemble de $k$ caractéristiques. Pour correspondre à l'exemple ci-dessus, une caractéristique pourrait indiquer à quel point un film est proche de la catégorie "film historiques"
- si on multiplie les caractéristiques des utilisateurs par celles des films (et fait les sommes adéquates), on aura une approximation raisonnable de l'évaluation d'un utilisateur pour un film

Ce qui est intéressant, c'est que l'on ne sait pas quelles sont ces caractéristiques, ni même combien d'entre elles sont pertinentes. On choisit un nombre $k$, et l'on apprend les valeurs des caractéristiques pour les utilisateurs et les films, en minimisant une fonction de perte.

Si notre utilisateur est représenté par un vecteur de dimension $k$, $\textbf{x}_{u}$, et un item par un vecteur de dimension $k$, $\textbf{y}_{i}$, la note prédite pour l'item par l'utilisateur est : 

$$\hat r_{ui} = \textbf{x}_{u}^{\intercal} \cdot{} \textbf{y}_{i} = \sum\limits_{k} x_{uk}y_{ki}$$

où $\hat r_{ui}$ représente la prédiction de la vraie note $r_{ui}$. $\textbf{y}_{i}$ est un vecteur colonne, $\textbf{x}_{u}^{\intercal}$ un vecteur ligne. On les appelle en général "vecteurs latents". Les *k* dimensions sont appelées les facteurs latents.

On cherche à minimiser le carré de la différence entre les notes de notre jeu de données et nos prédictions. La fonction à la forme suivante :

$$L = \sum\limits_{u,i \in S}(r_{ui} - \textbf{x}_{u}^{\intercal} \cdot{} \textbf{y}_{i})^{2} + \lambda_{x} \sum\limits_{u} \left\Vert \textbf{x}_{u} \right\Vert^{2} + \lambda_{y} \sum\limits_{u} \left\Vert \textbf{y}_{i} \right\Vert^{2}$$

On a ici ajouté deux termes de régularisation L2 pour limiter le sur-apprentissage (overfitting) des utilisateurs et des items. On va s'intéresser à deux manières de minimiser, à l'aide de l'ALS (Alternate Least Squares) et d'une SGD (Stochastic gradient descent).

## Alternating Least Squares

Pour réaliser l'ALS, on fixe les valeurs d'un ensemble de vecteurs latents. Nous allons par exemple garder constants les vecteurs d'items. On cherche quand la dérivée vaut 0, et on résout pour les vecteurs non constants (utilisateurs). Vient maintenant l'alternance : on va maintenant fixer ces nouveaux vecteurs utilisateurs, pour lesquels on a résolu l'équation, puis prendre la dérivée de la loss par rapport aux vecteurs anciennement constants. On fera cette alternance successivement jusqu'à convergence.

### Dérivation

Plus précisément : 

$$\frac{\partial L}{\partial \textbf{x}_{u}} = - 2 \sum\limits_{i}(r_{ui} - \textbf{x}_{u}^{\intercal} \cdot{} \textbf{y}_{i}) \textbf{y}_{i}^{\intercal} + 2 \lambda_{x} \textbf{x}_{u}^{\intercal}$$

$$0 = -(\textbf{r}_{u} - \textbf{x}_{u}^{\intercal} Y^{\intercal})Y + \lambda_{x} \textbf{x}_{u}^{\intercal}$$

$$\textbf{x}_{u}^{\intercal}(Y^{\intercal}Y + \lambda_{x}I) = \textbf{r}_{u}Y$$

$$\textbf{x}_{u}^{\intercal} = \textbf{r}_{u}Y(Y^{\intercal}Y + \lambda_{x}I)^{-1}$$

$Y$ (de dimensioins $m \times k$) représente tous les vecteurs-lignes pour les éléments mis l'un sous l'autre. Et le vecteur ligne $\textbf{r}_{u}$ représente la ligne de l'utilisateur $u$ de la matrice de ratings (dimensions $1 \times m$). Enfin, $I$ est la matrice identité, de dimension $\times k$.

La dérivation avec les vecteurs d'items est similaire : 
$$\frac{\partial L}{\partial \textbf{y}_{i}} = - 2 \sum\limits_{i}(r_{iu} - \textbf{y}_{i}^{\intercal} \cdot{} \textbf{x}_{u}) \textbf{x}_{u}^{\intercal} + 2 \lambda_{y} \textbf{y}_{i}^{\intercal}$$

$$0 = -(\textbf{r}_{i} - \textbf{y}_{i}^{\intercal} X^{\intercal})X + \lambda_{y} \textbf{y}_{i}^{\intercal}$$

$$ \textbf{y}_{i}^{\intercal} ( X^{\intercal}X +  \lambda_{y}I) =  \textbf{r}_{i} X$$

$$ \textbf{y}_{i}^{\intercal} =  \textbf{r}_{i} X  ( X^{\intercal}X +  \lambda_{y}I) ^{-1}$$

### Implémentation

On reprend les données précédentes, on recrée la matrice de notes, on découpe en train/test. On se donne une fonction pour calculer la MSE, qu'on optimisera.

In [ ]:
import numpy as np
import pandas as pd
np.random.seed(0)

In [ ]:
cd ml-100k/

In [ ]:
# chargement de données
names = ['user_id', 'item_id', 'rating', 'timestamp']
df = pd.read_csv('u.data', sep='\t', names=names)
n_users = df.user_id.unique().shape[0]
n_items = df.item_id.unique().shape[0]

# Matrice de notes
ratings = np.zeros((n_users, n_items))
for row in df.itertuples():
    ratings[row[1]-1, row[2]-1] = row[3]

# On découpe en train/tests, en prenant 10 notes
# de chaque utilisateur pour les placer en test
def train_test_split(ratings):
    test = np.zeros(ratings.shape)
    train = ratings.copy()
    for user in range(ratings.shape[0]):
        test_ratings = np.random.choice(ratings[user, :].nonzero()[0], 
                                        size=10, 
                                        replace=False)
        train[user, test_ratings] = 0.
        test[user, test_ratings] = ratings[user, test_ratings]
        
    # On s'assure que c'est disjoint
    assert(np.all((train * test) == 0)) 
    return train, test

train, test = train_test_split(ratings)

In [ ]:
from sklearn.metrics import mean_squared_error

def get_mse(pred, actual):
    # on ne calcule que sur les entrées non vides.
    pred = pred[actual.nonzero()].flatten()
    actual = actual[actual.nonzero()].flatten()
    return mean_squared_error(pred, actual)

On se dote maintenant d'une classe pour réaliser l'ALS.

In [ ]:
from numpy.linalg import solve

class ExplicitMF():
    def __init__(self, 
                 ratings, 
                 n_factors=40, 
                 item_reg=0.0, 
                 user_reg=0.0,
                 verbose=False):
        """
        Train a matrix factorization model to predict empty 
        entries in a matrix. The terminology assumes a 
        ratings matrix which is ~ user x item
        
        Params
        ======
        ratings : (ndarray)
            User x Item matrix with corresponding ratings
        
        n_factors : (int)
            Number of latent factors to use in matrix 
            factorization model
        
        item_reg : (float)
            Regularization term for item latent factors
        
        user_reg : (float)
            Regularization term for user latent factors
        
        verbose : (bool)
            Whether or not to printout training progress
        """
        
        self.ratings = ratings
        self.n_users, self.n_items = ratings.shape
        self.n_factors = n_factors
        self.item_reg = item_reg
        self.user_reg = user_reg
        self._v = verbose

    def als_step(self,
                 latent_vectors,
                 fixed_vecs,
                 ratings,
                 _lambda,
                 type='user'):
        """
        One of the two ALS steps. Solve for the latent vectors
        specified by type.
        """
        if type == 'user':
            # Precompute
            YTY = fixed_vecs.T.dot(fixed_vecs)
            lambdaI = np.eye(YTY.shape[0]) * _lambda

            for u in range(latent_vectors.shape[0]):
                latent_vectors[u, :] = solve((YTY + lambdaI), 
                                             ratings[u, :].dot(fixed_vecs))
        elif type == 'item':
            # Precompute
            XTX = fixed_vecs.T.dot(fixed_vecs)
            lambdaI = np.eye(XTX.shape[0]) * _lambda
            
            for i in range(latent_vectors.shape[0]):
                latent_vectors[i, :] = solve((XTX + lambdaI), 
                                             ratings[:, i].T.dot(fixed_vecs))
        return latent_vectors

    def train(self, n_iter=10):
        """ Train model for n_iter iterations from scratch."""
        # initialize latent vectors
        self.user_vecs = np.random.random((self.n_users, self.n_factors))
        self.item_vecs = np.random.random((self.n_items, self.n_factors))
        
        self.partial_train(n_iter)
    
    def partial_train(self, n_iter):
        """ 
        Train model for n_iter iterations. Can be 
        called multiple times for further training.
        """
        ctr = 1
        while ctr <= n_iter:
            if ctr % 10 == 0 and self._v:
                print('\tcurrent iteration: {}'.format(ctr))
            self.user_vecs = self.als_step(self.user_vecs, 
                                           self.item_vecs, 
                                           self.ratings, 
                                           self.user_reg, 
                                           type='user')
            self.item_vecs = self.als_step(self.item_vecs, 
                                           self.user_vecs, 
                                           self.ratings, 
                                           self.item_reg, 
                                           type='item')
            ctr += 1
    
    def predict_all(self):
        """ Predict ratings for every user and item. """
        predictions = np.zeros((self.user_vecs.shape[0], 
                                self.item_vecs.shape[0]))
        for u in range(self.user_vecs.shape[0]):
            for i in range(self.item_vecs.shape[0]):
                predictions[u, i] = self.predict(u, i)
                
        return predictions
    def predict(self, u, i):
        """ Single user and item prediction. """
        return self.user_vecs[u, :].dot(self.item_vecs[i, :].T)
    
    def calculate_learning_curve(self, iter_array, test):
        """
        Keep track of MSE as a function of training iterations.
        
        Params
        ======
        iter_array : (list)
            List of numbers of iterations to train for each step of 
            the learning curve. e.g. [1, 5, 10, 20]
        test : (2D ndarray)
            Testing dataset (assumed to be user x item).
        
        The function creates two new class attributes:
        
        train_mse : (list)
            Training data MSE values for each value of iter_array
        test_mse : (list)
            Test data MSE values for each value of iter_array
        """
        iter_array.sort()
        self.train_mse =[]
        self.test_mse = []
        iter_diff = 0
        for (i, n_iter) in enumerate(iter_array):
            if self._v:
                print('Iteration: {}'.format(n_iter))
            if i == 0:
                self.train(n_iter - iter_diff)
            else:
                self.partial_train(n_iter - iter_diff)

            predictions = self.predict_all()

            self.train_mse += [get_mse(predictions, self.ratings)]
            self.test_mse += [get_mse(predictions, test)]
            if self._v:
                print('Train MSE: ' + str(self.train_mse[-1]))
                print('Test MSE: ' + str(self.test_mse[-1]))
            iter_diff = n_iter

On commence par un premier entraînement avec $k=40$, sans régularisation. On va ensuite tracer la courbe de la MSE en fonction des itérations.

In [ ]:
MF_ALS = ExplicitMF(train, n_factors=40, \
                    user_reg=0.0, item_reg=0.0)

# attention, un peu long : 
# on peut limiter les itérations
iter_array = [1, 2, 5, 10, 25, 50, 100]

MF_ALS.calculate_learning_curve(iter_array, test)

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()

def plot_learning_curve(iter_array, model):
    plt.plot(iter_array, model.train_mse, \
             label='Training', linewidth=5)
    plt.plot(iter_array, model.test_mse, \
             label='Test', linewidth=5)


    plt.xticks(fontsize=16);
    plt.yticks(fontsize=16);
    plt.xlabel('iterations', fontsize=30);
    plt.ylabel('MSE', fontsize=30);
    plt.legend(loc='best', fontsize=20);

In [ ]:
plot_learning_curve(iter_array, MF_ALS)

**Question :** Que concluez-vous ?

### Optimisons

#### Régularisation

Proposons un peu de régularisation, pour améliorer.

**Question :** Ajoutez ci-dessous une cellule pour relancer le calcul, avec cette fois un peu de régularisation. Tracez ensuite la courbe, comme précédemment.

**Question:** Que s'est-il passé ?

#### Grid search
Effectuons une petite grid-search pour trouver de bons paramètres pour la régularisation et le nombre de facteurs latents. Pour simplifier, les paramètres de régularisation seront les mêmes (utilisateurs et items).

In [ ]:
latent_factors = [5, 10, 20, 40, 80]
regularizations = [0.01, 0.1, 1., 10., 100.]
regularizations.sort()
iter_array = [1, 2, 5, 10, 25, 50, 100]

best_params = {}
best_params['n_factors'] = latent_factors[0]
best_params['reg'] = regularizations[0]
best_params['n_iter'] = 0
best_params['train_mse'] = np.inf
best_params['test_mse'] = np.inf
best_params['model'] = None

for fact in latent_factors:
    print('Factors: {}'.format(fact))
    for reg in regularizations:
        print('Regularization: {}'.format(reg))
        MF_ALS = ExplicitMF(train, n_factors=fact, \
                            user_reg=reg, item_reg=reg)
        MF_ALS.calculate_learning_curve(iter_array, test)
        min_idx = np.argmin(MF_ALS.test_mse)
        if MF_ALS.test_mse[min_idx] < best_params['test_mse']:
            best_params['n_factors'] = fact
            best_params['reg'] = reg
            best_params['n_iter'] = iter_array[min_idx]
            best_params['train_mse'] = MF_ALS.train_mse[min_idx]
            best_params['test_mse'] = MF_ALS.test_mse[min_idx]
            best_params['model'] = MF_ALS
            print('New optimal hyperparameters')
            print(pd.Series(best_params))

In [ ]:
best_als_model = best_params['model']
plot_learning_curve(iter_array, best_als_model)

**Question :** Quels sont les meilleurs paramètres ?

## La SGD (Stochastic Gradient Descent)

Avec la SGD, on utilise à nouveau les dérivées partielles de la fonction de loss, mais on les calcule par rapport à chaque variable. La partie "stochastique" de l'algorithme repose sur une mise à jour des poids un échantillon à la fois. Pour chaque échantillon, on prend la dérivée par rapport à chaque variable, résout en zéro pour les poids donnés et on met à jour.

On va utiliser la même fonction que précédemment, mais ajouter quelques détails au modèle : au lieu de considérer que l'évaluation de chaque utilisateur pour un item est simplement le produit de leurs vecteurs latents, on va 
ajouter un terme de biais, pour prendre en compte le fait que certains utilisateurs notent *toujours haut*, et que certains films ont des notes *toujours basses*. On va ajouter un petit terme de biais global ($\mu$). Notre note prédite se calcule ainsi :

$$ \hat r_{ui} = \mu + b_{u} + b_{i} + \textbf{x}_{u}^{\intercal} \cdot{} \textbf{y}_{i} $$

où $b_{u}$ ($b_{i}$) est le bias utilisateur (item).

Notre fonction de _loss_ devient :
$$L = \sum\limits_{u,i}(r_{ui} - (\mu + b_{u} + b_{i} + \textbf{x}_{u}^{\intercal} \cdot{} \textbf{y}_{i}))^{2} + 
\lambda_{xb} \sum\limits_{u} \left\Vert b_{u} \right\Vert^{2} + \lambda_{yb} \sum\limits_{i} \left\Vert b_{i} \right\Vert^{2} + \lambda_{xf} \sum\limits_{u} \left\Vert \textbf{x}_{u} \right\Vert^{2} + \lambda_{yf} \sum\limits_{u} \left\Vert \textbf{y}_{i} \right\Vert^{2}$$

(On a ajouté les termes de régularisation des biais)

On veut mettre à jour chaque caractéristique (les facteurs latents utilisateurs et item, les biais) à chaque échantillon. La mise à jour du biais utilisateur est donnée par :
$$ b_{u} \leftarrow b_{u} - \eta \frac{\partial L}{\partial b_{u}} $$
où $\eta$ est le pas d'apprentissage, qui pondère comment chaque mise à jour va modifier les poids de chaque caractéristique. 

La dérivée partielle vaut :
$$ \frac{\partial L}{\partial b_{u}} = 2(r_{ui} - (\mu + b_{u} + b_{i} + \textbf{x}_{u}^{\intercal} \cdot{} \textbf{y}_{i}))(-1) + 2\lambda_{xb} b_{u} $$
$$ \frac{\partial L}{\partial b_{u}} = 2(e_{ui})(-1) + 2\lambda_{xb} b_{u} $$
$$ \frac{\partial L}{\partial b_{u}} = - e_{ui} + \lambda_{xb} b_{u} $$

où $e_{ui}$ représente l'erreur de prédiction. 

Les mises à jour complètes sont donc :

$$ b_{u} \leftarrow b_{u} + \eta \, (e_{ui} - \lambda_{xb} b_{u}) $$
$$ b_{i} \leftarrow b_{i} + \eta \, (e_{ui} - \lambda_{yb} b_{i}) $$
$$ \textbf{x}_{u} \leftarrow \textbf{x}_{u} + \eta \, (e_{ui}\textbf{y}_{i} - \lambda_{xf} \textbf{x}_{u}) $$
$$ \textbf{y}_{i} \leftarrow \textbf{y}_{i} + \eta \, (e_{ui}\textbf{x}_{u} - \lambda_{yf} \textbf{y}_{i}) $$

### Implémentation

Reprenons la classe ci-dessus, en ajoutant la possibilité de faire la mise à jour selon la SGD.

In [ ]:
class ExplicitMF():
    def __init__(self, 
                 ratings,
                 n_factors=40,
                 learning='sgd',
                 item_fact_reg=0.0, 
                 user_fact_reg=0.0,
                 item_bias_reg=0.0,
                 user_bias_reg=0.0,
                 verbose=False):
        """
        Train a matrix factorization model to predict empty 
        entries in a matrix. The terminology assumes a 
        ratings matrix which is ~ user x item
        
        Params
        ======
        ratings : (ndarray)
            User x Item matrix with corresponding ratings
        
        n_factors : (int)
            Number of latent factors to use in matrix 
            factorization model
        learning : (str)
            Method of optimization. Options include 
            'sgd' or 'als'.
        
        item_fact_reg : (float)
            Regularization term for item latent factors
        
        user_fact_reg : (float)
            Regularization term for user latent factors
            
        item_bias_reg : (float)
            Regularization term for item biases
        
        user_bias_reg : (float)
            Regularization term for user biases
        
        verbose : (bool)
            Whether or not to printout training progress
        """
        
        self.ratings = ratings
        self.n_users, self.n_items = ratings.shape
        self.n_factors = n_factors
        self.item_fact_reg = item_fact_reg
        self.user_fact_reg = user_fact_reg
        self.item_bias_reg = item_bias_reg
        self.user_bias_reg = user_bias_reg
        self.learning = learning
        if self.learning == 'sgd':
            self.sample_row, self.sample_col = self.ratings.nonzero()
            self.n_samples = len(self.sample_row)
        self._v = verbose

    def als_step(self,
                 latent_vectors,
                 fixed_vecs,
                 ratings,
                 _lambda,
                 type='user'):
        """
        One of the two ALS steps. Solve for the latent vectors
        specified by type.
        """
        if type == 'user':
            # Precompute
            YTY = fixed_vecs.T.dot(fixed_vecs)
            lambdaI = np.eye(YTY.shape[0]) * _lambda

            for u in range(latent_vectors.shape[0]):
                latent_vectors[u, :] = solve((YTY + lambdaI), 
                                             ratings[u, :].dot(fixed_vecs))
        elif type == 'item':
            # Precompute
            XTX = fixed_vecs.T.dot(fixed_vecs)
            lambdaI = np.eye(XTX.shape[0]) * _lambda
            
            for i in range(latent_vectors.shape[0]):
                latent_vectors[i, :] = solve((XTX + lambdaI), 
                                             ratings[:, i].T.dot(fixed_vecs))
        return latent_vectors

    def train(self, n_iter=10, learning_rate=0.1):
        """ Train model for n_iter iterations from scratch."""
        # initialize latent vectors        
        self.user_vecs = np.random.normal(scale=1./self.n_factors,\
                                          size=(self.n_users, self.n_factors))
        self.item_vecs = np.random.normal(scale=1./self.n_factors,
                                          size=(self.n_items, self.n_factors))
        
        if self.learning == 'als':
            self.partial_train(n_iter)
        elif self.learning == 'sgd':
            self.learning_rate = learning_rate
            self.user_bias = np.zeros(self.n_users)
            self.item_bias = np.zeros(self.n_items)
            self.global_bias = np.mean(self.ratings[np.where(self.ratings != 0)])
            self.partial_train(n_iter)
    
    
    def partial_train(self, n_iter):
        """ 
        Train model for n_iter iterations. Can be 
        called multiple times for further training.
        """
        ctr = 1
        while ctr <= n_iter:
            if ctr % 10 == 0 and self._v:
                print('\tcurrent iteration: {}'.format(ctr))
            if self.learning == 'als':
                self.user_vecs = self.als_step(self.user_vecs, 
                                               self.item_vecs, 
                                               self.ratings, 
                                               self.user_fact_reg, 
                                               type='user')
                self.item_vecs = self.als_step(self.item_vecs, 
                                               self.user_vecs, 
                                               self.ratings, 
                                               self.item_fact_reg, 
                                               type='item')
            elif self.learning == 'sgd':
                self.training_indices = np.arange(self.n_samples)
                np.random.shuffle(self.training_indices)
                self.sgd()
            ctr += 1

    def sgd(self):
        for idx in self.training_indices:
            u = self.sample_row[idx]
            i = self.sample_col[idx]
            prediction = self.predict(u, i)
            e = (self.ratings[u,i] - prediction) # error
            
            # Update biases
            self.user_bias[u] += self.learning_rate * \
                                (e - self.user_bias_reg * self.user_bias[u])
            self.item_bias[i] += self.learning_rate * \
                                (e - self.item_bias_reg * self.item_bias[i])
            
            #Update latent factors
            self.user_vecs[u, :] += self.learning_rate * \
                                    (e * self.item_vecs[i, :] - \
                                     self.user_fact_reg * self.user_vecs[u,:])
            self.item_vecs[i, :] += self.learning_rate * \
                                    (e * self.user_vecs[u, :] - \
                                     self.item_fact_reg * self.item_vecs[i,:])
    def predict(self, u, i):
        """ Single user and item prediction."""
        if self.learning == 'als':
            return self.user_vecs[u, :].dot(self.item_vecs[i, :].T)
        elif self.learning == 'sgd':
            prediction = self.global_bias + self.user_bias[u] + self.item_bias[i]
            prediction += self.user_vecs[u, :].dot(self.item_vecs[i, :].T)
            return prediction
    
    def predict_all(self):
        """ Predict ratings for every user and item."""
        predictions = np.zeros((self.user_vecs.shape[0], 
                                self.item_vecs.shape[0]))
        for u in range(self.user_vecs.shape[0]):
            for i in range(self.item_vecs.shape[0]):
                predictions[u, i] = self.predict(u, i)
                
        return predictions
    
    def calculate_learning_curve(self, iter_array, test, learning_rate=0.1):
        """
        Keep track of MSE as a function of training iterations.
        
        Params
        ======
        iter_array : (list)
            List of numbers of iterations to train for each step of 
            the learning curve. e.g. [1, 5, 10, 20]
        test : (2D ndarray)
            Testing dataset (assumed to be user x item).
        
        The function creates two new class attributes:
        
        train_mse : (list)
            Training data MSE values for each value of iter_array
        test_mse : (list)
            Test data MSE values for each value of iter_array
        """
        iter_array.sort()
        self.train_mse =[]
        self.test_mse = []
        iter_diff = 0
        for (i, n_iter) in enumerate(iter_array):
            if self._v:
                print('Iteration: {}'.format(n_iter))
            if i == 0:
                self.train(n_iter - iter_diff, learning_rate)
            else:
                self.partial_train(n_iter - iter_diff)

            predictions = self.predict_all()

            self.train_mse += [get_mse(predictions, self.ratings)]
            self.test_mse += [get_mse(predictions, test)]
            if self._v:
                print('Train mse: ' + str(self.train_mse[-1]))
                print('Test mse: ' + str(self.test_mse[-1]))
            iter_diff = n_iter

Comme avec l'ALS plus tôt, commençons avec 40 facteurs latents, sans régularisation et un pas de 0.001.

In [ ]:
MF_SGD = ExplicitMF(train, 40, learning='sgd', verbose=True)
iter_array = [1, 2, 5, 10, 25, 50, 100, 200]
MF_SGD.calculate_learning_curve(iter_array, test, learning_rate=0.001)

In [ ]:
plot_learning_curve(iter_array, MF_SGD)

**Question :** Que concluez-vous de ces résultats ?

### Optimisations

Optimisons un peu, avec une grid-search pour le pas d'apprentissage.

In [ ]:
iter_array = [1, 2, 5, 10, 25, 50, 100, 200]
learning_rates = [1e-5, 1e-4, 1e-3, 1e-2]

best_params = {}
best_params['learning_rate'] = None
best_params['n_iter'] = 0
best_params['train_mse'] = np.inf
best_params['test_mse'] = np.inf
best_params['model'] = None


for rate in learning_rates:
    print('Rate: {}'.format(rate))
    MF_SGD = ExplicitMF(train, n_factors=40, learning='sgd')
    MF_SGD.calculate_learning_curve(iter_array, test, learning_rate=rate)
    min_idx = np.argmin(MF_SGD.test_mse)
    if MF_SGD.test_mse[min_idx] < best_params['test_mse']:
        best_params['n_iter'] = iter_array[min_idx]
        best_params['learning_rate'] = rate
        best_params['train_mse'] = MF_SGD.train_mse[min_idx]
        best_params['test_mse'] = MF_SGD.test_mse[min_idx]
        best_params['model'] = MF_SGD
        print('New optimal hyperparameters')
        print(pd.Series(best_params))

**Question :** Qu'obtenez-vous ?

On peut aussi chercher à optimiser les autres hyperparamètres (termes de régularisation et facteurs latents). Cela pourrait être parallélisé, ça prend un peu de temps.

In [ ]:
# sera sans doute un peu long pendant la séance

iter_array = [1, 2, 5, 10, 25, 50, 100, 200]
latent_factors = [5, 10, 20, 40, 80]
regularizations = [0.001, 0.01, 0.1, 1.]
regularizations.sort()

best_params = {}
best_params['n_factors'] = latent_factors[0]
best_params['reg'] = regularizations[0]
best_params['n_iter'] = 0
best_params['train_mse'] = np.inf
best_params['test_mse'] = np.inf
best_params['model'] = None

for fact in latent_factors:
    print('Factors: {}'.format(fact))
    for reg in regularizations:
        print('Regularization: {}'.format(reg))
        MF_SGD = ExplicitMF(train, n_factors=fact, learning='sgd',\
                            user_fact_reg=reg, item_fact_reg=reg, \
                            user_bias_reg=reg, item_bias_reg=reg)
        MF_SGD.calculate_learning_curve(iter_array, test, learning_rate=0.001)
        min_idx = np.argmin(MF_SGD.test_mse)
        if MF_SGD.test_mse[min_idx] < best_params['test_mse']:
            best_params['n_factors'] = fact
            best_params['reg'] = reg
            best_params['n_iter'] = iter_array[min_idx]
            best_params['train_mse'] = MF_SGD.train_mse[min_idx]
            best_params['test_mse'] = MF_SGD.test_mse[min_idx]
            best_params['model'] = MF_SGD
            print('New optimal hyperparameters')
            print(pd.Series(best_params))

In [ ]:
plot_learning_curve(iter_array, best_params['model'])

In [ ]:
print('Best regularization: {}'.format(best_params['reg']))
print('Best latent factors: {}'.format(best_params['n_factors']))
print('Best iterations: {}'.format(best_params['n_iter']))

**Question :** Qu'obtenez-vous ? Que pourrait-on faire ?

## Les recommandations proposées

On va, comme précédemment, essayer de regarder "à l'œil", la qualité des recommandations proposées, en listant 5 recommandations pour un film donné.

On commence par entraîner nos modèles avec l'ALS et la SGD, avec nos meilleurs paramètres.

In [ ]:
best_als_model = ExplicitMF(ratings, n_factors=20, learning='als', \
                            item_fact_reg=0.01, user_fact_reg=0.01)
best_als_model.train(50)

In [ ]:
best_sgd_model = ExplicitMF(ratings, n_factors=80, learning='sgd', \
                            item_fact_reg=0.01, user_fact_reg=0.01, \
                            user_bias_reg=0.01, item_bias_reg=0.01)
best_sgd_model.train(200, learning_rate=0.001)

On calcule une similarité cosinus "film à film" sur les deux matrices des modèles :

In [ ]:
def cosine_similarity(model):
    sim = model.item_vecs.dot(model.item_vecs.T)
    norms = np.array([np.sqrt(np.diagonal(sim))])
    return sim / norms / norms.T

als_sim = cosine_similarity(best_als_model)
sgd_sim = cosine_similarity(best_sgd_model)

On va maintenant chercher, pour un film donné, 5 recommandations avec chaque modèle.

In [ ]:
idx_to_movie = {}
with open('u.item', 'r', encoding="utf8", errors='ignore') as f:
    for line in f.readlines():
        info = line.split('|')
        idx_to_movie[int(info[0])-1] = info[1]

In [ ]:
def top_k_movies(similarity, mapper, movie_idx, k=6):
    return [mapper[x] for x in np.argsort(similarity[movie_idx,:])[:-k-1:-1]]

def print_top_k_movies(movies):
    for k,movie in enumerate(movies[1:]): # on sort le film d'entrée lui-même
        print("%s : %s"%(k+1,movie)) #on affiche avec décalage d'indice

In [ ]:
from IPython.display import HTML
from IPython.display import display

def compare_recs(als_similarity, sgd_similarity, mapper,\
                 movie_idx, k=5):
    display(HTML('<font size=3>'+'Entrée : '+idx_to_movie[movie_idx]+'</font>'))
    # ALS
    display(HTML('<font size=3>'+'Recommandations avec ALS :'+'</font>'))
    print_top_k_movies(top_k_movies(als_similarity, idx_to_movie, movie_idx))
    # SGD
    display(HTML('<font size=3>'+'Recommandations avec SGD :'+'</font>'))
    
    print_top_k_movies(top_k_movies(sgd_similarity, idx_to_movie, movie_idx))

In [ ]:
idx = 0 # Toy Story
compare_recs(als_sim, sgd_sim, idx_to_movie, idx)

In [ ]:
idx = 1 # GoldenEye
compare_recs(als_sim, sgd_sim, idx_to_movie, idx)

In [ ]:
idx = 20 # Muppet Treasure Island
compare_recs(als_sim, sgd_sim, idx_to_movie, idx)

In [ ]:
idx = 500 # Dumbo
compare_recs(als_sim, sgd_sim, idx_to_movie, idx)

**Question :** Que concluez-vous ?